# Importação de bibliotecas

In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import plotly.express as px
import warnings
warnings.filterwarnings('ignore')
from datetime import date, datetime

# Abertura do arquivo de títulos

In [2]:
titulos = pd.read_csv(r"C:\Users\rodli\OneDrive\Documentos\Mestrado\Arquivos\Titulos_data.csv", sep=';', encoding='utf-8')

# Corte de arquivo por data

### Permite fazer a análise de qualquer período de data - Titulos

In [3]:
#data_inicio = '02-08-2023'
data_inicio = '02-08-2023'
data_inicio_titulo = data_inicio
data_inicio = datetime.strptime(data_inicio, '%d-%m-%Y').date()
data_fim = '16-04-2024'
data_fim_titulo = data_fim
data_fim = datetime.strptime(data_fim, '%d-%m-%Y').date()
titulos['data_corte'] = ''
for ind in range(0, len(titulos)):
    titulos['data_corte'][ind] = datetime.strptime(titulos['Data'][ind], '%d/%m/%Y').date()
titulos = titulos[titulos['data_corte'] >= data_inicio]
titulos = titulos[titulos['data_corte'] <= data_fim]

# Definindo o array de buscas no arquivo

### Qualquer palavra ou frase pode ser colocada no array de buscas

In [4]:
buscas = ['Alianza Lima', 'Colo Colo', 'Cerro Portenho', 'Alianza de Lima', 'Palmeiras']
#buscas = ['Botafogo', 'Flamengo', 'Internacional', 'Palmeiras', 'Vasco', 'Bayern de Munique']
#buscas = ['America MG', 'Athletico PR', 'Atletico MG', 'Bahia', 'Botafogo', 'Coritiba', 'Corinthians', 'Cruzeiro', 'Flamengo',
#          'Gremio', 'Internacional', 'Palmeiras', 'Bragantino', 'Sao Paulo', 'Santos', 'Vasco', 'Fortaleza', 'Olimpia', 
#          'Cuiaba', 'Goias', 'Boca Juniors', 'LDU', 'Bayern de Munique', 'Volta Redonda', 'Portuguesa']
#buscas = ['Branca', 'Tricolor', 'Camisa']
#buscas = ['Arias', 'Cano', 'Fábio', 'Ganso']

## Seleção de palavra chave no arquivo de título

In [5]:
buscas = sorted(buscas)
rodada = 0
colunas = ['Título', 'Extenso', 'Sessões', 'Usuários', 'Novos usuários', 'Data', 'nome_busca', 'nome']
pag_buscaf = pd.DataFrame(columns=colunas)
for ind in range(0, len(buscas)):
    nome = buscas[ind]
    titulos['nome_busca'] = titulos.Título.str.contains(nome)
    pag_busca1 = titulos.query("nome_busca == True")
    pag_busca1['nome'] = buscas[ind]
    rodada = rodada + 1
    if rodada == 0:
        pag_buscaf = pag_busca1
    else:
        pag_buscaf = pd.concat([pag_buscaf, pag_busca1])
    titulos['nome_busca'] = False
pag_buscaf = pag_buscaf.drop(['Título', 'Usuários', 'Novos usuários', 'nome_busca'], axis=1)
print(pag_buscaf)

              Data   Extenso Sessões  data_corte          nome
93171   20/03/2024  20240320      11  2024-03-20  Alianza Lima
93259   23/03/2024  20240323       3  2024-03-23  Alianza Lima
93571   22/03/2024  20240322       2  2024-03-22  Alianza Lima
93681   20/03/2024  20240320       1  2024-03-20  Alianza Lima
93682   20/03/2024  20240320       1  2024-03-20  Alianza Lima
...            ...       ...     ...         ...           ...
103096  08/04/2024  20240408       1  2024-04-08     Palmeiras
103097  12/04/2024  20240412       1  2024-04-12     Palmeiras
103098  10/04/2024  20240410       1  2024-04-10     Palmeiras
103099  13/04/2024  20240413       1  2024-04-13     Palmeiras
103100  12/04/2024  20240412       1  2024-04-12     Palmeiras

[1281 rows x 5 columns]


### Agrupa saída por data

In [6]:
pag_buscaf = pag_buscaf.groupby(['Extenso', 'Data', 'nome'], as_index=False).sum()
pag_buscaf = pag_buscaf.sort_values(by=['Extenso', 'Data', 'nome'], ascending=True)
pag_buscaf = pag_buscaf.reset_index(drop=True)

### Complementa busca por palavra-chave zerando datas não encontradas

In [7]:
final = []
array_data = pag_buscaf.Data.unique()
array_ext = pag_buscaf.Extenso.unique()
for ind2 in range(0, len(array_data)):
    for ind in range(0, len(buscas)):
        result = pag_buscaf.loc[pag_buscaf['nome'] == buscas[ind]]
        result = result.loc[result['Data'] == array_data[ind2]]
        if len(result) == 0:
            insert = (array_ext[ind2], array_data[ind2], buscas[ind], 0)
            final.append(insert)
colunas = ['Extenso', 'Data', 'nome', 'Sessões']
pag_buscaf_aux = pd.DataFrame(data=final, columns=colunas)
pag_buscaf = pd.concat([pag_buscaf, pag_buscaf_aux], sort=True)

### Reordena por data e palavra-chave

In [8]:
pag_buscaf = pag_buscaf.sort_values(by=['Extenso', 'Data', 'nome'], ascending=True)
pag_buscaf = pag_buscaf.reset_index(drop=True)

### Relatório de acessos diários por palavra-chave

In [33]:
fig = px.line(pag_buscaf, x="Data", y="Sessões", color='nome', title='Padrão de acesso ao próximo adversário', markers=True)
fig.update_layout(xaxis_tickangle=-45)
fig.write_html(r"C:\Users\rodli\OneDrive\Documentos\Mestrado\Arquivos\Graficos\Adversarios_acessos_" + str(data_inicio_titulo) + "_" + str(data_fim_titulo) + ".html")
fig.show()

## Identifica palavra chave mais acessada no geral

In [10]:
pag_geral = pag_buscaf.groupby(['nome'], as_index=False).sum()
pag_geral = pag_geral.sort_values(by=['Sessões', 'nome'], ascending=False)
pag_geral = pag_geral.reset_index(drop=True)
fig = px.bar(pag_geral, x='nome', y='Sessões', title='Adversários mais acessados geral de ' + str(data_inicio_titulo) + ' até ' + str(data_fim_titulo), color='Sessões')
fig.update_layout(xaxis_tickangle=-45, height=700)
fig.write_html(r"C:\Users\rodli\OneDrive\Documentos\Mestrado\Arquivos\Graficos\Adversarios_mais_acessos_geral_" + str(data_inicio_titulo) + "_" + str(data_fim_titulo) + ".html")
fig.show()

# Títulos mais acessados (30)

In [11]:
pag_buscag = titulos.groupby('Título', as_index=False).sum()
pag_buscag = pag_buscag.sort_values(by='Sessões', ascending=False)
pag_buscag = pag_buscag.reset_index(drop=True)

In [12]:
pag_buscag_hd30 = pag_buscag.head(30)
fig = px.bar(pag_buscag_hd30, x='Título', y='Sessões', color='Título', title='Mais acessadas de ' + str(data_inicio_titulo) + ' até ' + str(data_fim_titulo))
fig.update_layout(xaxis_tickangle=-45)
fig.write_html(r"C:\Users\rodli\OneDrive\Documentos\Mestrado\Arquivos\Graficos\Titulos_acessos_geral_" + str(data_inicio_titulo) + "_" + str(data_fim_titulo) + ".html")
fig.show()

# Títulos mais acessados sem a página Inicial e páginas principais de consulta 

In [13]:
titulos_ordenado = titulos.sort_values(by=['Extenso','Sessões','Título'], ascending=False)
titulos_ordenado = titulos_ordenado.reset_index(drop=True)

### Consolidado por data e título - Títulos mais acessados na data

In [14]:
from plotly.subplots import make_subplots
import plotly.graph_objects as go

datas = titulos_ordenado.data_corte.unique()
tamanho = len(datas)
lista_del = ['Estatisticas Fluminense - Principal', 'Especiais', 'Adversarios', 'Jogador', 'Arbitros', 'Estadios', 'Jogo', 
             'Especiais Adversarios', 'Consultas Especiais', 'Especiais Jogadores', 'Especiais Estadios', 'Especiais Gerais',
             'Especiais Jogos', 'Graficos', 'Campeonatos', 'Tecnico', 'Mascotes', 'Estatísticas Fluminense - Principal',
             'Adversários', 'Árbitros','Técnicos','Estádios','Especiais Adversários', 'Especiais Estádios', 'Técnico',
             'Especiais Técnicos', 'Especiais Sequências', 'Gráficos', 'Especiais Tecnico']

for ind2 in range(0, len(lista_del)):
    titulos_ordenado = titulos_ordenado[titulos_ordenado['Título'] != lista_del[ind2]]


for ind in range(0, tamanho):
    dt_wk = datas[ind]
    graf_wk = titulos_ordenado[titulos_ordenado['data_corte'] == dt_wk]
    graf_wk = graf_wk[titulos_ordenado['Título'] != lista_del[0]]
    graf_wk = graf_wk.head(15)
    titulo = 'Títulos mais acessados em ' + str(dt_wk)
    fig = px.bar(graf_wk, x='Título', y='Sessões', title=titulo, color='Sessões')
    fig.update_layout(xaxis_tickangle=-45, height=500)
    fig.write_html(r"C:\Users\rodli\OneDrive\Documentos\Mestrado\Arquivos\Graficos\Titulos_mais_acessos_" + str(dt_wk) + ".html")
    fig.show()

### Consolidados Geral titulo e data - Títulos mais acessados em 1 dia

In [15]:
titulos2 = titulos
lista_del2 = ['Estatisticas Fluminense - Principal', 'Especiais', 'Adversarios', 'Jogador', 'Arbitros', 'Estadios', 'Jogo', 
             'Especiais Adversarios', 'Consultas Especiais', 'Especiais Jogadores', 'Especiais Estadios', 'Especiais Gerais',
             'Especiais Jogos', 'Graficos', 'Campeonatos', 'Tecnico', 'Mascotes', 'Estatísticas Fluminense - Principal',
             'Adversários', 'Árbitros','Técnicos','Estádios','Especiais Adversários', 'Especiais Estádios', 'Técnico',
             'Especiais Técnicos', 'Especiais Sequências', 'Gráficos', 'Especiais Tecnico']

for ind2 in range(0, len(lista_del2)):
    titulos2 = titulos2[titulos2['Título'] != lista_del2[ind2]]


In [16]:
titulos_jogos_data = titulos2.groupby(by=['Título', 'Data'], as_index=False).sum()
titulos_jogos_data['agrupado'] = titulos_jogos_data['Título'] + '-' + titulos_jogos_data['Data']
titulos_jogos_data = titulos_jogos_data.sort_values(by='Sessões', ascending=False)
titulos_jogos_data = titulos_jogos_data.reset_index(drop=True)
titulos_jogos_data_30 = titulos_jogos_data.head(30)

In [17]:
fig = px.bar(titulos_jogos_data_30, x='agrupado', y='Sessões', title='Títulos mais acessados por data de ' + str(data_inicio_titulo) + ' até ' + str(data_fim_titulo), color='Sessões')
fig.update_layout(xaxis_tickangle=-45, height=700)
fig.write_html(r"C:\Users\rodli\OneDrive\Documentos\Mestrado\Arquivos\Graficos\Titulos_mais_acessos_dia_" + str(data_inicio_titulo) + "_" + str(data_fim_titulo) + ".html")
fig.show()

# Análise de Adversários - Páginas do confronto mais acessadas

#### Análises específicas do site legado objeto do estudo

In [18]:
abcd = 'Fluminense x '
pag_buscag['nome_busca'] = pag_buscag.Título.str.contains(abcd)
pag_busca1 = pag_buscag.query("nome_busca == True")
pag_busca1 = pag_busca1.sort_values(by='Sessões', ascending=False)
pag_busca1 = pag_busca1.reset_index(drop=True)
pag_busca1_hd30 = pag_busca1.head(15)

In [19]:
fig = px.bar(pag_busca1_hd30, x='Título', y='Sessões', title='Adversários mais visitados de ' + str(data_inicio_titulo) + ' até ' + str(data_fim_titulo), color='Sessões')
fig.update_layout(xaxis_tickangle=-45, height=700)
fig.write_html(r"C:\Users\rodli\OneDrive\Documentos\Mestrado\Arquivos\Graficos\Adversarios_mais_acessos_" + str(data_inicio_titulo) + "_" + str(data_fim_titulo) + ".html")
fig.show()

# Técnicos mais acessados

In [20]:
abcd = 'Tec - '
pag_buscag['nome_busca'] = pag_buscag.Título.str.contains(abcd)
pag_busca1 = pag_buscag.query("nome_busca == True")
pag_busca1 = pag_busca1.sort_values(by='Sessões', ascending=False)
pag_busca1 = pag_busca1.reset_index(drop=True)
pag_busca1_hd30 = pag_busca1.head(15)

In [21]:
fig = px.bar(pag_busca1_hd30, x='Título', y='Sessões', title='Técnicos mais visitados de ' + str(data_inicio_titulo) + ' até ' + str(data_fim_titulo), color='Título')
fig.update_layout(xaxis_tickangle=-45, height=600)
fig.write_html(r"C:\Users\rodli\OneDrive\Documentos\Mestrado\Arquivos\Graficos\Tecnicos_mais_acessos_" + str(data_inicio_titulo) + "_" + str(data_fim_titulo) + ".html")
fig.show()

## Análises onde a palavra chave estão relacionados aos anos possíveis

#### Específica para o site legado objeto do estudo que engloba os anos de 1902 até presente

In [22]:
buscas = ['2024','2023','2022','2021','2020','2019','2018','2017','2016','2015','2014','2013','2012','2011','2010','2009','2008',
'2007','2006','2005','2004','2003','2002','2001','2000','1999','1998','1997','1996','1995','1994','1993','1992','1991','1990',
'1989','1988','1987','1986','1985','1984','1983','1982','1981','1980','1979','1978','1977','1976','1975','1974','1973','1972',
'1971','1970','1969','1968','1967','1966','1965','1964','1963','1962','1961','1960','1959','1958','1957','1956','1955','1954',
'1953','1952','1951','1950','1949','1948','1947','1946','1945','1944','1943','1942','1941','1940','1939','1938','1937','1936',
'1935','1934','1933','1932','1931','1930','1929','1928','1927','1926','1925','1924','1923','1922','1921','1920','1919','1918',
'1917','1916','1915','1914','1913','1912','1911','1910','1909','1908','1907','1906','1905','1904','1903','1902']
buscas = sorted(buscas)
rodada = 0
colunas = ['Título', 'Extenso', 'Sessões', 'Usuários', 'Novos usuários', 'Data', 'nome_busca', 'nome']
pag_busca_barra = pd.DataFrame(columns=colunas)
for ind in range(0, len(buscas)):
    nome = buscas[ind]
    titulos['nome_busca'] = titulos.Título.str.contains(nome)
    pag_busca1 = titulos.query("nome_busca == True")
    pag_busca1['nome'] = buscas[ind]
    rodada = rodada + 1
    if rodada == 0:
        pag_busca_barra = pag_busca1
    else:
        pag_busca_barra = pd.concat([pag_busca_barra, pag_busca1])
    titulos['nome_busca'] = False
pag_busca_barra = pag_busca_barra.drop(['Extenso', 'Data', 'Usuários', 'Novos usuários', 'nome_busca', 'nome'], axis=1)

In [23]:
pag_busca_barra = pag_busca_barra.groupby(by='Título', as_index=False).sum()
pag_busca_barra = pag_busca_barra.sort_values(by='Sessões', ascending=False)
pag_busca_barra = pag_busca_barra.reset_index(drop=True)
pag_busca_barra_hd30 = pag_busca_barra.head(30)

In [24]:
fig = px.bar(pag_busca_barra_hd30, x='Título', y='Sessões', title='Consultas que envolvam ANO de ' + str(data_inicio_titulo) + ' até ' + str(data_fim_titulo), color='Sessões')
fig.update_layout(xaxis_tickangle=-45, height=700)
fig.write_html(r"C:\Users\rodli\OneDrive\Documentos\Mestrado\Arquivos\Graficos\Titulos_ano_acessos_" + str(data_inicio_titulo) + "_" + str(data_fim_titulo) + ".html")
fig.show()

## Análises por palavra chave única

### Camisa por data

In [25]:
titulo_arb = titulos
variavel = 'Paulo Goulart'
titulo_arb['Variavel'] = titulo_arb.Título.str.contains(variavel)
titulo_arb_filtrado = titulo_arb.query("Variavel == True")
titulo_arb_filtrado = titulo_arb_filtrado.sort_values(by='Sessões', ascending=False)
titulo_arb_filtrado = titulo_arb_filtrado.reset_index(drop=True)
titulo_arb_agrup = titulo_arb_filtrado
titulo_arb_agrup['agrupado'] = titulo_arb_agrup['Título'] + '-' + titulo_arb_agrup['Data']
titulo_arb_agrup = titulo_arb_agrup.head(30)

fig = px.bar(titulo_arb_agrup, x='agrupado', y='Sessões', title='Consultas que envolvam ' + variavel +  ' de ' + str(data_inicio_titulo) + ' até ' + str(data_fim_titulo), color='Sessões')
fig.update_layout(xaxis_tickangle=-45, height=700)
fig.write_html(r"C:\Users\rodli\OneDrive\Documentos\Mestrado\Arquivos\Graficos\Acessos_data_" + variavel + "_" + str(data_inicio_titulo) + "_" + str(data_fim_titulo) + ".html")
fig.show()


### Camisa Geral

In [26]:
titulo_arb_filtrado = titulo_arb_filtrado.groupby(by='Título', as_index=False).sum()
titulo_arb_filtrado = titulo_arb_filtrado.sort_values(by='Sessões', ascending=False)
titulo_arb_filtrado = titulo_arb_filtrado.reset_index(drop=True)

fig = px.bar(titulo_arb_filtrado, x='Título', y='Sessões', title='Consultas que envolvam ' + variavel + ' de ' + str(data_inicio_titulo) + ' até ' + str(data_fim_titulo), color='Sessões')
fig.update_layout(xaxis_tickangle=-45, height=700)
fig.write_html(r"C:\Users\rodli\OneDrive\Documentos\Mestrado\Arquivos\Graficos\Acessos_" + variavel + "_" + str(data_inicio_titulo) + "_" + str(data_fim_titulo) + ".html")
fig.show()

### Maracanã por data

In [27]:
titulo_arb = titulos
variavel = 'Maracana'
titulo_arb['Variavel'] = titulo_arb.Título.str.contains(variavel)
titulo_arb_filtrado = titulo_arb.query("Variavel == True")
titulo_arb_filtrado = titulo_arb_filtrado.sort_values(by='Sessões', ascending=False)
titulo_arb_filtrado = titulo_arb_filtrado.reset_index(drop=True)
titulo_arb_agrup = titulo_arb_filtrado
titulo_arb_agrup['agrupado'] = titulo_arb_agrup['Título'] + '-' + titulo_arb_agrup['Data']
titulo_arb_agrup = titulo_arb_agrup.head(30)

fig = px.bar(titulo_arb_agrup, x='agrupado', y='Sessões', title='Consultas que envolvam ' + variavel +  ' de ' + str(data_inicio_titulo) + ' até ' + str(data_fim_titulo), color='Sessões')
fig.update_layout(xaxis_tickangle=-45, height=700)
fig.write_html(r"C:\Users\rodli\OneDrive\Documentos\Mestrado\Arquivos\Graficos\Acessos_data_" + variavel + "_" + str(data_inicio_titulo) + "_" + str(data_fim_titulo) + ".html")
fig.show()

### Maracanã Geral

In [28]:
titulo_arb_filtrado = titulo_arb_filtrado.groupby(by='Título', as_index=False).sum()
titulo_arb_filtrado = titulo_arb_filtrado.sort_values(by='Sessões', ascending=False)
titulo_arb_filtrado = titulo_arb_filtrado.reset_index(drop=True)

fig = px.bar(titulo_arb_filtrado, x='Título', y='Sessões', title='Consultas que envolvam ' + variavel +  ' de ' + str(data_inicio_titulo) + ' até ' + str(data_fim_titulo), color='Sessões')
fig.update_layout(xaxis_tickangle=-45, height=700)
fig.write_html(r"C:\Users\rodli\OneDrive\Documentos\Mestrado\Arquivos\Graficos\Acessos_" + variavel + "_" + str(data_inicio_titulo) + "_" + str(data_fim_titulo) + ".html")
fig.show()

### Por data

In [29]:
titulo_arb = titulos
variavel = 'Zagalo'
titulo_arb['Variavel'] = titulo_arb.Título.str.contains(variavel)
titulo_arb_filtrado = titulo_arb.query("Variavel == True")
titulo_arb_filtrado = titulo_arb_filtrado.sort_values(by='Sessões', ascending=False)
titulo_arb_filtrado = titulo_arb_filtrado.reset_index(drop=True)
titulo_arb_agrup = titulo_arb_filtrado
titulo_arb_agrup['agrupado'] = titulo_arb_agrup['Título'] + '-' + titulo_arb_agrup['Data']
titulo_arb_agrup = titulo_arb_agrup.head(30)

fig = px.bar(titulo_arb_agrup, x='agrupado', y='Sessões', title='Consultas que envolvam ' + variavel +  ' de ' + str(data_inicio_titulo) + ' até ' + str(data_fim_titulo), color='Sessões')
fig.update_layout(xaxis_tickangle=-45, height=700)
fig.write_html(r"C:\Users\rodli\OneDrive\Documentos\Mestrado\Arquivos\Graficos\Acessos_data_" + variavel + "_" + str(data_inicio_titulo) + "_" + str(data_fim_titulo) + ".html")
fig.show()

### Geral

In [30]:
titulo_arb_filtrado = titulo_arb_filtrado.groupby(by='Título', as_index=False).sum()
titulo_arb_filtrado = titulo_arb_filtrado.sort_values(by='Sessões', ascending=False)
titulo_arb_filtrado = titulo_arb_filtrado.reset_index(drop=True)

fig = px.bar(titulo_arb_filtrado, x='Título', y='Sessões', title='Consultas que envolvam ' + variavel +  ' de ' + str(data_inicio_titulo) + ' até ' + str(data_fim_titulo), color='Sessões')
fig.update_layout(xaxis_tickangle=-45, height=700)
fig.write_html(r"C:\Users\rodli\OneDrive\Documentos\Mestrado\Arquivos\Graficos\Acessos_" + variavel + "_" + str(data_inicio_titulo) + "_" + str(data_fim_titulo) + ".html")
fig.show()

In [31]:
titulo_arb = titulos
variavel = 'Wilmar Roldan'
titulo_arb['Variavel'] = titulo_arb.Título.str.contains(variavel)
titulo_arb_filtrado = titulo_arb.query("Variavel == True")
titulo_arb_filtrado = titulo_arb_filtrado.sort_values(by='Sessões', ascending=False)
titulo_arb_filtrado = titulo_arb_filtrado.reset_index(drop=True)
titulo_arb_agrup = titulo_arb_filtrado
titulo_arb_agrup['agrupado'] = titulo_arb_agrup['Título'] + '-' + titulo_arb_agrup['Data']
titulo_arb_agrup = titulo_arb_agrup.head(30)

fig = px.bar(titulo_arb_agrup, x='agrupado', y='Sessões', title='Consultas que envolvam ' + variavel +  ' de ' + str(data_inicio_titulo) + ' até ' + str(data_fim_titulo), color='Sessões')
fig.update_layout(xaxis_tickangle=-45, height=700)
fig.write_html(r"C:\Users\rodli\OneDrive\Documentos\Mestrado\Arquivos\Graficos\Acessos_data_" + variavel + "_" + str(data_inicio_titulo) + "_" + str(data_fim_titulo) + ".html")
fig.show()

In [32]:
titulo_arb_filtrado = titulo_arb_filtrado.groupby(by='Título', as_index=False).sum()
titulo_arb_filtrado = titulo_arb_filtrado.sort_values(by='Sessões', ascending=False)
titulo_arb_filtrado = titulo_arb_filtrado.reset_index(drop=True)

fig = px.bar(titulo_arb_filtrado, x='Título', y='Sessões', title='Consultas que envolvam ' + variavel +  ' de ' + str(data_inicio_titulo) + ' até ' + str(data_fim_titulo), color='Sessões')
fig.update_layout(xaxis_tickangle=-45, height=700)
fig.write_html(r"C:\Users\rodli\OneDrive\Documentos\Mestrado\Arquivos\Graficos\Acessos_" + variavel + "_" + str(data_inicio_titulo) + "_" + str(data_fim_titulo) + ".html")
fig.show()